# Import 

In [12]:
import pandas as pd
import re
import numpy as np
from tqdm import tqdm

from fuzzywuzzy import process, fuzz
from const import (
    LABEL_PATTERN_1_V2,
    LABEL_PATTERN_2_V2
)

# Cleaning IndoT5 Result

In [13]:
df = pd.read_csv("output\IndoT5-smallv2-validation-testing-v4.csv").drop(columns=['Unnamed: 0', 'label'])
df = pd.read_csv("output\IndoT5-basev2-validation-testing-v4.csv").drop(columns=['Unnamed: 0', 'label'])
df = pd.read_csv("output\IndoT5-bparav2-validation-testing-v4.csv").drop(columns=['Unnamed: 0', 'label'])
# df = pd.read_csv("output\IndoT5-largev2-validation-testing-v4.csv").drop(columns=['Unnamed: 0', 'label'])

In [14]:
def clean_result(text):
    text = text.strip().strip("</s>").strip("<pad>").strip()

    return text


def extract_parts(text):

    label_splitted1 = re.findall(LABEL_PATTERN_1_V2, text)
    label_splitted2 = re.findall(LABEL_PATTERN_2_V2, text)

    if label_splitted1 != []:
        label_splitted = label_splitted1[0]
    elif label_splitted2 != []:
        label_splitted = (label_splitted2[0][0], "NULL", label_splitted2[0][1])
    else:
        label_splitted = ("NULL", "NULL", "NULL")

    return label_splitted

def element_atribution(df):
    df_copy = df.copy()

    for index, row in df_copy.iterrows():
        label_splitted = extract_parts(row['IndoT5_result'])

        df_copy.at[index, 'speaker_result'] = label_splitted[0]
        df_copy.at[index, 'target_result'] = label_splitted[1]
        df_copy.at[index, 'sentiment_result'] = label_splitted[2]

    return df_copy


def clean_quotation_result(news):
    quotation = news.split("\n\n")[-1]

    return quotation

def clean_target_result(target):
    if target == 'Umum' or target == 'nan':
        target = "NULL"

    return target


def filter_df(df):
    df_copy = df.copy()
    
    keyword = [
        "Anies", "Baswedan", "Muhaimin", "Iskandar", "Cak Imin", "Amin",
        "Ganjar", "Pranowo", "Mahfud", "MD",
        "Prabowo", "Subianto", "Gibran", "Rakabuming", "Raka"
    ]

    df_copy = df_copy[df_copy['text'].apply(lambda x: any(word.lower() in x.lower() for word in keyword))]

    print(f"Len before: {len(df)}")
    print(f"Len after: {len(df_copy)}")
    
    return df_copy

df_result = df.copy()

df_result['IndoT5_result'] = df_result['IndoT5_result'].apply(clean_result)
df_result['quotation_result'] = df_result['text'].apply(clean_quotation_result)
df_result = element_atribution(df_result)
df_result['target_result'] = df_result['target_result'].apply(clean_target_result)
df_result = filter_df(df_result)

df_result

Len before: 251
Len after: 251


text  \
0    Laporan Wartawan Tribunnews.com, Igman Ibrahim...   
1    Laporan Wartawan Tribunnews.com, Igman Ibrahim...   
2    Laporan Wartawan Tribunnews.com, Igman Ibrahim...   
3    Laporan Wartawan Tribunnews.com, Fersianus Wak...   
4    Laporan Wartawan Tribunnews.com, Fersianus Wak...   
..                                                 ...   
246  Jakarta -  Viral sosok bernama Sappe yang curh...   
247  Jakarta -  Viral sosok bernama Sappe yang curh...   
248  Jakarta -  Viral sosok bernama Sappe yang curh...   
249  Jakarta -  Viral sosok bernama Sappe yang curh...   
250  TRIBUNNEWS.COM - Calon wakil presiden (Cawapre...   

                                         IndoT5_result  \
0    (' Prabowo' ;' Pihak yang tidak setuju Program...   
1    (' Prabowo' ;' Pihak yang tidak setuju Program...   
2    (' Prabowo' ;' Pihak yang menyatakan program m...   
3                  (' Ganjar' ;' Jokowi' ;' Positif' )   
4                 (' Jokowi' ;' Menteri' ;' Neutral' )   
..                                                 ...   
246         (' Sappe' ;' Anies Baswedan' ;' Positif' )   
247         (' Sappe' ;' Anies Baswedan' ;' Positif' )   
248                (' Sappe' ;' Netizen' ;' Neutral' )   
249  (' Sappe' ;' Masyarakat miskin di Parepare' ;'...   
250        (' Mahfud MD' ;' Uncle Usman' ;' Negatif' )   

                                      quotation_result speaker_result  \
0    "Saya katakan nanti siapa yang mau masuk kabin...        Prabowo   
1    "Yang tidak setuju mungkin sebaiknya belajar l...        Prabowo   
2    "Saudara-saudara sekalian yang mengatakan maka...        Prabowo   
3    "Terima kasih Pak Jokowi karena sampai dengan ...         Ganjar   
4    "Hak demokrasi, hak politik setiap orang. Seti...         Jokowi   
..                                                 ...            ...   
246  "Soal saya menangis, itu tidak dibuat-buat, gi...          Sappe   
247  "Kami nelayan dan masyarakat Parepare menitip ...          Sappe   
248  "Ya karena saya nelayan saya harus berpenampil...          Sappe   
249  "Sebelum saya menjadi caleg saya memang nelaya...          Sappe   
250  "Sehingga Mas Gibran lolos dengan melanggar et...      Mahfud MD   

                                         target_result sentiment_result  
0    Pihak yang tidak setuju Program Makan Siang Gr...          Negatif  
1    Pihak yang tidak setuju Program Makan Siang Gr...          Negatif  
2     Pihak yang menyatakan program makan siang gratis          Negatif  
3                                               Jokowi          Positif  
4                                              Menteri          Neutral  
..                                                 ...              ...  
246                                     Anies Baswedan          Positif  
247                                     Anies Baswedan          Positif  
248                                            Netizen          Neutral  
249                      Masyarakat miskin di Parepare          Neutral  
250                                        Uncle Usman          Negatif  

[251 rows x 6 columns]

# Pairing With The Correct Label

In [15]:
df_label = pd.read_csv("output\Validation Dataset Correct Annotation_v4.csv")

# rename column
df_label = df_label.rename(columns={
    'quotation': 'quotation_label',
    'speaker': 'speaker_label',
    'target': 'target_label',
    'sentiment': 'sentiment_label',
})


df_label['quotation_result'] = "NULL"
df_label['speaker_result'] = "NULL"
df_label['target_result'] = "NULL"
df_label['sentiment_result'] = "NULL"

for index_label, row_label in df_label.iterrows():
    for index_result, row_result in df_result.iterrows():
        if row_result['quotation_result'].strip() == row_label['quotation_label'].strip():
            df_label.at[index_label, 'quotation_result'] = row_result['quotation_result']
            df_label.at[index_label, 'speaker_result'] = row_result['speaker_result']
            df_label.at[index_label, 'target_result'] = row_result['target_result']
            df_label.at[index_label, 'sentiment_result'] = row_result['sentiment_result']

df_label = df_label.fillna("NULL")
df_label

body  \
0    Laporan Wartawan Tribunnews.com, Igman Ibrahim...   
1    Laporan Wartawan Tribunnews.com, Igman Ibrahim...   
2    Laporan Wartawan Tribunnews.com, Igman Ibrahim...   
3    Laporan Wartawan Tribunnews.com, Fersianus Wak...   
4    Laporan Wartawan Tribunnews.com, Fersianus Wak...   
..                                                 ...   
249  TRIBUNNEWS.COM, JAKARTA - Pernyataan Calon Pre...   
250  TRIBUNNEWS.COM, JAKARTA - Pernyataan Calon Pre...   
251  TRIBUNNEWS.COM - Calon wakil presiden (Cawapre...   
252  Suara.com - Geliat politik elite pasca- Pemilu...   
253  Suara.com - Geliat politik elite pasca- Pemilu...   

                                       quotation_label  \
0    "Saya katakan nanti siapa yang mau masuk kabin...   
1    "Yang tidak setuju mungkin sebaiknya belajar l...   
2    "Saudara-saudara sekalian yang mengatakan maka...   
3    "Terima kasih Pak Jokowi karena sampai dengan ...   
4    "Hak demokrasi, hak politik setiap orang. Seti...   
..                                                 ...   
249  "Bagaimana perasaan Mas Prabowo? Soal etik, et...   
250  Anies Baswedan menanggapi pertanyaan wartawan ...   
251  "Sehingga Mas Gibran lolos dengan melanggar et...   
252  "Semua, semua (akan diundang bertemu)," kata J...   
253                         "Semua diundang," katanya.   

                      speaker_label                          target_label  \
0                           Prabowo                         Calon Menteri   
1                           Prabowo  Penentang Program Makan Siang Gratis   
2                           Prabowo  Penentang Program Makan Siang Gratis   
3    Ganjar Pranowo;Cawapres Ganjar                                Jokowi   
4                            Jokowi                               menteri   
..                              ...                                   ...   
249                  Anies Baswedan                      Prabowo Subianto   
250                Prabowo Subianto                        Anies Baswedan   
251                       Mahfud Md                           Uncle Usman   
252                          Jokowi                    Semua elite parpol   
253                          Jokowi                    Semua elite parpol   

    sentiment_label                                   quotation_result  \
0           Negatif  "Saya katakan nanti siapa yang mau masuk kabin...   
1           Negatif  "Yang tidak setuju mungkin sebaiknya belajar l...   
2           Negatif  "Saudara-saudara sekalian yang mengatakan maka...   
3           Positif  "Terima kasih Pak Jokowi karena sampai dengan ...   
4           Neutral  "Hak demokrasi, hak politik setiap orang. Seti...   
..              ...                                                ...   
249         Negatif  "Bagaimana perasaan Mas Prabowo? Soal etik, et...   
250         Negatif                                               NULL   
251         Negatif  "Sehingga Mas Gibran lolos dengan melanggar et...   
252         Neutral  "Semua, semua (akan diundang bertemu)," kata J...   
253         Neutral                         "Semua diundang," katanya.   

     speaker_result                                      target_result  \
0           Prabowo  Pihak yang tidak setuju Program Makan Siang Gr...   
1           Prabowo  Pihak yang tidak setuju Program Makan Siang Gr...   
2           Prabowo   Pihak yang menyatakan program makan siang gratis   
3            Ganjar                                             Jokowi   
4            Jokowi                                            Menteri   
..              ...                                                ...   
249  Anies Baswedan                                            Prabowo   
250            NULL                                               NULL   
251       Mahfud MD                                        Uncle Usman   
252          Jokowi                                       Semua parpol   
253          Jokowi         

# Scoring

In [16]:
def name_similarity_score(target_name, other_names):
    
    if target_name == "NULL" and other_names == "NULL":
        return 100
    
    if target_name == "NULL" or other_names == "NULL":
        return 0
    
    similarities = []
    if ";" in other_names:
        other_names = other_names.split(";")
    else:
        other_names = [other_names]

    similarities = process.extractOne(target_name, other_names, scorer=fuzz.WRatio)
    

    return similarities[1]

In [17]:
df_evaluation = df_label.copy()

df_evaluation['speaker_score'] = 0
df_evaluation['target_score'] = 0
df_evaluation['sentiment_score'] = 0
df_evaluation['quotation_score'] = 0

for i, row in df_evaluation.iterrows():
    if row['quotation_result'].strip() == row['quotation_label'].strip():
        df_evaluation.at[i, 'quotation_score'] = 100
        
    if row['sentiment_result'] == row['sentiment_label']:
        df_evaluation.at[i, 'sentiment_score'] = 100

    df_evaluation.at[i, 'speaker_score'] = name_similarity_score(row['speaker_result'], row['speaker_label'])
    df_evaluation.at[i, 'target_score'] = name_similarity_score(row['target_result'], row['target_label'])

df_evaluation = df_evaluation.sort_values(by=['speaker_score', 'target_score', 'sentiment_score'], ascending=False)

print("Sentiment Accuracy: ", "{:.2f} %".format(df_evaluation['sentiment_score'].mean()))
print("Speaker Accuracy: ", "{:.2f} %".format(df_evaluation['speaker_score'].apply(lambda x: 100 if x >= 70 else 0).mean()))
print("Target Accuracy: ", "{:.2f} %".format(df_evaluation['target_score'].apply(lambda x: 100 if x >= 70 else 0).mean()))

print()
# print("Speaker Mean: ", df_evaluation['speaker_score'].mean())
# print("Target Mean: ", df_evaluation['target_score'].mean())


print()
print("Total Exrtacted Quotatin", df_result.shape[0])
print("Total Correct Quotation", df_label.shape[0])
print()
print("Correct Quotation: ", df_evaluation['quotation_score'].apply(lambda x: 1 if x == 100 else 0).sum())
print("Correct Sentiment: ", df_evaluation['sentiment_score'].apply(lambda x: 1 if x == 100 else 0).sum())
print("Correct Speaker: ", df_evaluation['speaker_score'].apply(lambda x: 1 if x >= 70 else 0).sum())
print("Correct Target: ", df_evaluation['target_score'].apply(lambda x: 1 if x >= 70 else 0).sum())


# display(df_evaluation.head(50))
# df_evaluation.loc[50:]

df_evaluation.to_csv("output\IndoT5-bparav2-evaluation-testing-v4.csv", index=False)

Sentiment Accuracy:  80.71 %
Speaker Accuracy:  98.43 %
Target Accuracy:  75.20 %


Total Exrtacted Quotatin 251
Total Correct Quotation 254

Correct Quotation:  251
Correct Sentiment:  205
Correct Speaker:  250
Correct Target:  191


In [18]:
df_check_result = df_result.copy()
df_check_result['quotation_score'] = 0
df_check_result['speaker_score'] = 0
df_check_result['target_score'] = 0
df_check_result['sentiment_score'] = 0

for i, row in df_check_result.iterrows():
    for j, row_label in df_label.iterrows():
        if row['quotation_result'].strip() == row_label['quotation_label'].strip():
            df_check_result.at[i, 'quotation_label'] = row_label['quotation_label']
            df_check_result.at[i, 'speaker_label'] = row_label['speaker_label']
            df_check_result.at[i, 'target_label'] = row_label['target_label']
            df_check_result.at[i, 'sentiment_label'] = row_label['sentiment_label']
            df_check_result.at[i, 'quotation_score'] = 100
        
            if row['sentiment_result'] == row_label['sentiment_label']:
                df_check_result.at[i, 'sentiment_score'] = 100

            df_check_result.at[i, 'speaker_score'] = name_similarity_score(row['speaker_result'], row_label['speaker_label'])
            df_check_result.at[i, 'target_score'] = name_similarity_score(row['target_result'], row_label['target_label'])


print("Correct Quotation: ", df_check_result['quotation_score'].apply(lambda x: 1 if x == 100 else 0).sum())
print("Correct Sentiment: ", df_check_result['sentiment_score'].apply(lambda x: 1 if x == 100 else 0).sum())
print("Correct Speaker: ", df_check_result['speaker_score'].apply(lambda x: 1 if x >= 70 else 0).sum())
print("Correct Target: ", df_check_result['target_score'].apply(lambda x: 1 if x >= 70 else 0).sum())


df_check_result[df_check_result['speaker_score'] >= 70].to_csv("output\IndoT5-basev2-validation-testing-v4-correct-speaker.csv")
df_check_result.to_csv("output\IndoT5-basev2-validation-testing-v4-check-target.csv")
df_check_result[df_check_result['sentiment_score'] == 100].to_csv("output\IndoT5-basev2-validation-testing-v4-correct-sentiment.csv")

Correct Quotation:  250
Correct Sentiment:  204
Correct Speaker:  249
Correct Target:  190


In [19]:
df_documment_level = df_check_result.copy()
df_documment_level['news'] = df_documment_level['text'].apply(lambda x: x.split("\n\n")[0])
df_documment_level = df_documment_level.groupby('news').agg({
    'quotation_score': 'mean',
    'speaker_score': 'mean',
    'target_score': 'mean',
    'sentiment_score': 'mean',
})

print("Quotation Score Mean    :", df_documment_level['quotation_score'].mean())
print("Speaker Score Mean      :", df_documment_level['speaker_score'].mean())
print("Target Score Mean       :", df_documment_level['target_score'].mean())
print("Sentiment Score Mean    :", df_documment_level['sentiment_score'].mean())
print()


print("Correct Quotation: ", df_documment_level['quotation_score'].apply(lambda x: 1 if x == 100 else 0).sum())
print("Correct Sentiment: ", df_documment_level['sentiment_score'].apply(lambda x: 1 if x == 100 else 0).sum())
print("Correct Speaker: ", df_documment_level['speaker_score'].apply(lambda x: 1 if x >= 70 else 0).sum())
print("Correct Target: ", df_documment_level['target_score'].apply(lambda x: 1 if x >= 70 else 0).sum())


Quotation Score Mean    : 99.6
Speaker Score Mean      : 98.51650793650792
Target Score Mean       : 82.92744444444445
Sentiment Score Mean    : 83.56666666666668

Correct Quotation:  49
Correct Sentiment:  26
Correct Speaker:  50
Correct Target:  39


## Quotation

In [20]:
for index, row in df_check_result.sort_values(by=['quotation_score'], ascending=False).iterrows():
    print("Index            : ", index)
    print("New              : ", row['text'])
    print("Quotation Result : ", row['quotation_result'])
    print("Quotation Label  : ", row['quotation_label'])
    print("="*40)

Index            :  0
New              :  Laporan Wartawan Tribunnews.com, Igman Ibrahim  TRIBUNNEWS.COM, JAKARTA - Capres nomor urut 2, Prabowo Subianto meminta pihak yang mau bergabung menjadi menteri pada kabinet yang akan dipimpinnya harus setuju dengan program makan siang gratis bagi anak-anak yang digagasnya.  Ketua Umum Partai Gerindra itu menyampaikan pihak yang tidak setuju dengan program makan siang gratis seharusnya tidak mengajukan diri masuk ke dalam kabinetnya.  "Saya katakan nanti siapa yang mau masuk kabinet siapa yang mau menjadi menteri saya harus setuju anak-anak harus diberi makan siang kalau kau tidak setuju nggak usah gabung di kabinet Prabowo Subianto," kata Prabowo dalam sambutannya di hadapan puluhan ribu pendukungnya di Stadion GBK, Senayan, Jakarta, Sabtu (10/2/2024).  Ia menuturkan bahwa perjuangan paslon nomor urut 2 sudah sedari awal ingin membawa program makan siang gratis untuk anak-anak Indonesia. Dia pun menuding yang tak setuju program itu sebagai keb

In [21]:
# print quoatation result and quotation label
for index, row in df_evaluation.sort_values(by=['quotation_score'], ascending=False).iterrows():
    print("Index        : ", index)
    print("New          : ", row['body'])
    print("Quotation Res:", row['quotation_result'])
    print("Quotation Lab:", row['quotation_label'])
    print("Score        : ", row['quotation_score'])
    print("="*40)

Index        : 

 4
New          :  Laporan Wartawan Tribunnews.com, Fersianus Waku  TRIBUNNEWS.COM, SEMARANG - Calon presiden (capres) nomor urut 3, Ganjar Pranowo mengucapkan terima kasih kepada Presiden Joko Widodo (Jokowi) karena tidak ikut berkampanye selama 75 hari masa kampanye Pilpres 2024.  "Terima kasih Pak Jokowi karena sampai dengan titik terakhir beliau tidak mengambil kesempatan itu (kampanye)," kata Ganjar seusai kampanye di Lapangan Pancasila, Simpang Lima Semarang, Jawa Tengah, Sabtu (10/2/2024).  Ganjar juga berterima kasih kepada kelompok masyarakat sipil yang selalu mengingatkan agar presiden tak berkampanye.  Diketahui, Jokowi selama masa kampanye Pilpres 2024 dikritik kubu pasagan capres-cawapres nomor urut 1 Anies Basswedan-Muhaimin Iskandar dan nomor urut 3, Ganjar -Mahfud, hingga sivitas akademika lantaran tendensi mendukung capres-cawapres nomor urut 2, Prabowo Subianto -Gibran Rakabuming Raka.  Hal itu tidak terlepas dibawanya program kerja hingga visi misi pemerintahan Jokow

## Speaker

In [22]:
for index, row in df_check_result.sort_values(by=['speaker_score'], ascending=False).iterrows():
    print("Index            : ", index)
    print("New              : ", row['text'])
    print("Quotation        : ", row['quotation_result'])
    print("Speaker Result   : ", row['speaker_result'])
    print("Speaker Label    : ", row['speaker_label'])
    print("Speaker Score    : ", row['speaker_score'])
    print("="*40)

Index            :  0
New              :  Laporan Wartawan Tribunnews.com, Igman Ibrahim  TRIBUNNEWS.COM, JAKARTA - Capres nomor urut 2, Prabowo Subianto meminta pihak yang mau bergabung menjadi menteri pada kabinet yang akan dipimpinnya harus setuju dengan program makan siang gratis bagi anak-anak yang digagasnya.  Ketua Umum Partai Gerindra itu menyampaikan pihak yang tidak setuju dengan program makan siang gratis seharusnya tidak mengajukan diri masuk ke dalam kabinetnya.  "Saya katakan nanti siapa yang mau masuk kabinet siapa yang mau menjadi menteri saya harus setuju anak-anak harus diberi makan siang kalau kau tidak setuju nggak usah gabung di kabinet Prabowo Subianto," kata Prabowo dalam sambutannya di hadapan puluhan ribu pendukungnya di Stadion GBK, Senayan, Jakarta, Sabtu (10/2/2024).  Ia menuturkan bahwa perjuangan paslon nomor urut 2 sudah sedari awal ingin membawa program makan siang gratis untuk anak-anak Indonesia. Dia pun menuding yang tak setuju program itu sebagai keb

Index            :  129
New              :  Jakarta -  Capres nomor urut 3 Ganjar Pranowo menyebut 3 jenderal mencla-mencle terkait arah dukungan di pilpres 2024, salah satunya Menko Marves Luhut Binsar Pandjaitan. Jubir Luhut, Jodi Mahardi membela.  "Kami ingin menegaskan bahwa bukan sifat Menko Luhut untuk menca-mencle," kata Jodi kepada wartawan, Rabu (7/2/2024).  Jodi mengatakan apa yang dipilih Luhut saat ini karena keinginan terhadap keberlanjutan dan penyempurnaan dari berbagai program yang berjalan di pemerintahan Jokowi. Di antaranya hilirisasi dan pemerataan infrastruktur.  "Pilihan Pak Menko Luhut karena keinginan untuk melihat keberlanjutan dan penyempurnaan berbagai program dan inisiatif pemerintah saat ini termasuk upaya hilirisasi untuk meningkatkan nilai tambah produk dalam negeri, pembangunan infrastruktur yang merata," ujarnya.  Begitu juga dengan pembangunan pedesaan hingga jaminan kesehatan yang gratis. Serta program penguatan digitalisasi untuk memperkuat pencegaha

In [23]:
# print quoatation result and quotation label
for index, row in df_evaluation.sort_values(by=['speaker_score'], ascending=False).iterrows():
    print("Index        : ", index)
    print("New          : ", row['body'])
    print("Quotation    :", row['quotation_result'])
    print("Result       : ", row['speaker_result'])
    print("Label        : ", row['speaker_label'])
    print("Score        : ", row['speaker_score'])
    print("="*40)

Index        :  4
New          :  Laporan Wartawan Tribunnews.com, Fersianus Waku  TRIBUNNEWS.COM, SEMARANG - Calon presiden (capres) nomor urut 3, Ganjar Pranowo mengucapkan terima kasih kepada Presiden Joko Widodo (Jokowi) karena tidak ikut berkampanye selama 75 hari masa kampanye Pilpres 2024.  "Terima kasih Pak Jokowi karena sampai dengan titik terakhir beliau tidak mengambil kesempatan itu (kampanye)," kata Ganjar seusai kampanye di Lapangan Pancasila, Simpang Lima Semarang, Jawa Tengah, Sabtu (10/2/2024).  Ganjar juga berterima kasih kepada kelompok masyarakat sipil yang selalu mengingatkan agar presiden tak berkampanye.  Diketahui, Jokowi selama masa kampanye Pilpres 2024 dikritik kubu pasagan capres-cawapres nomor urut 1 Anies Basswedan-Muhaimin Iskandar dan nomor urut 3, Ganjar -Mahfud, hingga sivitas akademika lantaran tendensi mendukung capres-cawapres nomor urut 2, Prabowo Subianto -Gibran Rakabuming Raka.  Hal itu tidak terlepas dibawanya program kerja hingga visi misi pem

## Target

In [24]:
i = 0
for index, row in df_check_result.sort_values(by=['target_score'], ascending=False).iterrows():
    i += 1
    print("Index            : ", index, i)
    print("New              : ", row['text'])
    print("Quotation        : ", row['quotation_result'])
    print("Target Result    : ", row['target_result'])
    print("Target Label     : ", row['target_label'])
    print("Target Score     : ", row['target_score'])
    print("="*40)

Index            :  250 1
New              :  TRIBUNNEWS.COM - Calon wakil presiden (Cawapres) nomor urut 3, Mahfud MD, mengingatkan kepada Pengadilan Tata Usaha Negara (PTUN) untuk tak mengabulkan permohonan mantan Ketua Mahkamah Konstitusi (MK) Anwar Usman.  Diketahui paman Gibran Rakabuming Raka itu membuat pengaduan ke PTUN agar membatalkan putusan pencopotan dirinya sebagai Ketua MK.  Menanggapi hal itu, Mahfud menegaskan bahwa Usman terbukti melanggar etika yang sangat berat meskipun aturan terkait batas usia cawapres sah secara hukum.  "Sehingga Mas Gibran lolos dengan melanggar etika, tetapi secara konstitusi, oke keputusannya jalan, tetapi yang dihukum adalah siapa-siapa yang melanggar. Itulah sebabnya uncle Usman lalu diberhentikan. Dan sekarang uncle Usman mengadu ke PTUN, (menggugat ke PTUN) itu adalah tindakan yang salah lagi, karena PTUN itu hanya mengadili keputusan tata usaha negara yang bersifat konkret, individual dan final, untuk itu PTUN jangan main-main mengabulkan

In [25]:
# print quoatation result and quotation label
for index, row in df_evaluation.sort_values(by=['target_score'], ascending=False).iterrows():
    print("Index  : ", index)
    print("Quotation :", row['quotation_label'])
    print("Target : ", row['target_result'])
    print("Label  : ", row['target_label'])
    print("Score  : ", row['target_score'])
    print("="*40)

Index  :  4
Quotation : "Hak demokrasi, hak politik setiap orang. Setiap menteri sama saja," ujar Jokowi saat memberikan keterangan pers di Terminal Selatan Lanud Halim Perdanakusuma, Jakarta Timur, Rabu (24/1/2024).
Target :  Menteri
Label  :  menteri
Score  :  100
Index  :  168
Quotation : "Kalau mau menghemat anggaran harusnya IKN yang menggunakan anggaran yang cukup besar yang dialihkan bukan pesta demokrasi," sambung Iqbal.
Target :  IKN
Label  :  IKN
Score  :  100
Index  :  208
Quotation : "Saya lagi cuti sejak pemilu. Mungkin DPR RI bisa melakukan pemanggilan menteri-menteri terkait dengan keprihatinan itu," tuturnya.
Target :  DPR RI
Label  :  DPR RI
Score  :  100
Index  :  209
Quotation : "Kita memiliki kualitas Pemilu yang baik. Arti yang baik itu berkualitas, beradab, sudah sepantasnya kita memiliki itu," kata Surya Paloh saat berorasi di Lapangan Lumpue, Parepare, Sulawesi Selatan, Selasa (6/2/2024).
Target :  Pemilu
Label  :  Pemilu
Score  :  100
Index  :  211
Quotation : 

## Sentiment

In [26]:
# print quoatation result and quotation label
i = 0
for index, row in df_evaluation.sort_values(by=['sentiment_score'], ascending=False).iterrows():
    i += 1
    print("Index  : ", i)
    print("Quotation :", row['quotation_result'])
    print("Target : ", row['sentiment_result'])
    print("Label  : ", row['sentiment_label'])
    print("Score  : ", row['sentiment_score'])
    print("="*40)

Index  :  1
Quotation : "Hak demokrasi, hak politik setiap orang. Setiap menteri sama saja," ujar Jokowi saat memberikan keterangan pers di Terminal Selatan Lanud Halim Perdanakusuma, Jakarta Timur, Rabu (24/1/2024).
Target :  Neutral
Label  :  Neutral
Score  :  100
Index  :  2
Quotation : "Pasangan Ganjar-Mahfud mendapatkan nomor urut 3, nomor ini sesuai dengan nomor PDI Perjuagnan sebagai peserta pemilu legislatif. Sehingga secara teknis memudahkan bagi kami untuk berkampanye secara pararel, baik pemilu legislatif maupun pemilu presiden," ujarnya.
Target :  Positif
Label  :  Positif
Score  :  100
Index  :  3
Quotation : "Sangat mungkin karena tren kenaikkan AMIN selalu ada di setiap survei, tidak ada tren penurunan sedikit pun," kata Jazilul ditemui di Taman Rekreasi Selecta, Kota Batu, Jawa Timur, Minggu (31/12/2023).
Target :  Positif
Label  :  Positif
Score  :  100
Index  :  4
Quotation : "Diperkirakan sekitar Rp 15.000 per anak. Itu bisa bervariasi," ujar Airlangga saat diwawanca

In [27]:
# confusion matrix for sentiment
from sklearn.metrics import f1_score, classification_report

df_sentiment = df_check_result.copy().dropna()
true_labels = df_sentiment['sentiment_label']
pred_labels = df_sentiment['sentiment_result']

# Alternatively, you can get a detailed classification report
report = classification_report(true_labels, pred_labels)
print("\nClassification Report:")
print(report)

df_sentiment.groupby(['sentiment_label', 'sentiment_result']).size().unstack().fillna(0)


Classification Report:
              precision    recall  f1-score   support

     Negatif       0.75      0.83      0.79        66
     Neutral       0.80      0.73      0.76        91
     Positif       0.87      0.89      0.88        93

    accuracy                           0.82       250
   macro avg       0.81      0.82      0.81       250
weighted avg       0.82      0.82      0.82       250



sentiment_result  Negatif  Neutral  Positif
sentiment_label                            
Negatif                55       10        1
Neutral                14       66       11
Positif                 4        6       83

In [28]:
def filter_df(df):
    df_copy = df.copy()
    
    keyword = [
        "Anies", "Baswedan", "Muhaimin", "Iskandar", "Cak Imin", "Amin",
        "Ganjar", "Pranowo", "Mahfud", "MD",
        "Prabowo", "Subianto", "Gibran", "Rakabuming", "Raka"
    ]

    df_copy = df_copy[df_copy['body'].apply(lambda x: any(word.lower() in x.lower() for word in keyword))]

    print(f"Len before: {len(df)}")
    print(f"Len after: {len(df_copy)}")
    
    return df_copy

df_temp = pd.read_csv("output/Validation Dataset Correct Annotation_v3.csv")
# df_evaluation.to_csv("result.csv")
filter_df(df_temp)
df_temp

Len before: 271
Len after: 249


body  \
0    Suara.com - Pihak Istana buka suara soal jadwa...   
1    Suara.com - Pihak Istana buka suara soal jadwa...   
2    Suara.com - Pihak Istana buka suara soal jadwa...   
3    Suara.com - Pihak Istana buka suara soal jadwa...   
4    Suara.com - Pihak Istana buka suara soal jadwa...   
..                                                 ...   
266  TRIBUNNEWS.COM, JAKARTA - Capres nomor urut 2 ...   
267  Liputan6.com, Jakarta Calon Wakil Presiden Uru...   
268  Jakarta -  Survei Populi menyebut sebanyak 79,...   
269  Jakarta -  Survei Populi menyebut sebanyak 79,...   
270  Suara.com - Cawapres nomor urut 01, Muhaimain ...   

                                    quotation_sentence         speaker  \
0    "Rabu besok, 21 Februari 2024, pukul 11.00 WIB...   Ari Dwipayana   
1    "Mengenai siapa yang akan diangkat dan dilanti...   Ari Dwipayana   
2    "Selain itu, akan ada pengucapan sumpah/janji ...   Ari Dwipayana   
3    "Besok ditunggu saja jam 10," kata Jokowi Anco...     Joko Widodo   
4                 "Besok dilihat jam 10," kata Jokowi.     Joko Widodo   
..                                                 ...             ...   
266  "Saudara-saudara sekalian, semua pembaharuan, ...         Prabowo   
267  "(40 kota) ini dengan kemampuan menampung pend...        Muhaimin   
268  "Pada Feburari 2024, sebesar 79,9% responden m...  Muhammad Iqbal   
269  "Ketika ditanya lebih lanjut, mayoritas respon...  Muhammad Iqbal   
270  "PBNU sudah menerima dan marilah kita sama-sam...        Gus Ipul   

                   target sentiment  
0    Presiden Joko Widodo   Neutral  
1    Presiden Joko Widodo   Neutral  
2    Presiden Joko Widodo   Neutral  
3                    Umum   Neutral  
4                    Umum   Neutral  
..                    ...       ...  
266        anak-anak muda   Positif  
267              Muhaimin   Neutral  
268        lembaga survei   Negatif  
269             Responden   Negatif  
270                   PKB   Negatif  

[271 rows x 5 columns]